In [59]:
%matplotlib inline

# London tube dataset provided by: markdunne (github.com/markdunne)
# Bike dataset provided by: Transport for London

import colorsys
import random
import numpy as np
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
from collections import Counter
from bokeh.plotting import figure, show
from bokeh.resources import CDN
from bokeh.io import output_notebook
output_notebook( resources=CDN )
import math

pd.set_option('max_colwidth', 200)

Loading BokehJS ...

In [60]:
# Tube
lines       = pd.read_csv('london.lines.csv', index_col=0)
stations    = pd.read_csv('london.stations.csv', index_col=0)
stationsRein= pd.read_csv('london.stations.reindexed.csv', index_col=0)
connections = pd.read_csv('london.connections.csv')

# Bikes
bikeTripData = pd.read_csv('bikes/london-bikes-sorted.csv', index_col=0)     # http://cycling.data.tfl.gov.uk
bikeDockingStations = pd.read_csv('santander-cycle-coords.csv', index_col=0)   # https://tfl.gov.uk/tfl/syndication/feeds/cycle-hire/livecyclehireupdates.xml 

In [61]:
# Divide bike data into different files for quicker processing
# or rather, store indices of start/stop of data.
startOfBikeDataStartStationSection = {}
startOfBikeDataStartStationSection[1] = 0

currId = 1
for station_id, station in bikeTripData.iterrows():
    if currId == station["StartStation Id"]:
        continue
    else:
        startOfBikeDataStartStationSection[currId+1] = station_id
        currId = currId + 1
        

{1: 0, 2: 284, 3: 751, 4: 1322, 5: 1610, 6: 2264, 7: 2772, 8: 2969, 9: 3006, 10: 3466, 11: 3703, 12: 4156, 13: 5105, 14: 5428, 15: 8544, 16: 9037, 17: 9616, 18: 10346, 19: 11152, 20: 11573, 21: 12081, 22: 12249, 23: 12774, 24: 13113, 25: 13827, 26: 14494, 27: 14848, 28: 15415, 29: 15958, 30: 16315, 31: 16790, 32: 17251, 33: 18121, 34: 18642, 35: 18923, 36: 18924, 37: 19344, 38: 19800, 39: 20040, 40: 21077, 41: 21432, 42: 22168, 43: 22699, 44: 23115, 45: 23422, 46: 24042, 47: 24810, 48: 25299, 49: 26104, 50: 26372, 51: 26774, 52: 27100, 53: 27477, 54: 27734, 55: 28212, 56: 29514, 57: 29841, 58: 30360, 59: 30928, 60: 30929, 61: 31114, 62: 31470, 63: 31692, 64: 31997, 65: 32851, 66: 33223, 67: 34181, 68: 34718, 69: 35276, 70: 35624, 71: 35822, 72: 36818, 73: 37230, 74: 38299, 75: 39167, 76: 39624, 77: 39857, 78: 40336, 79: 40905, 80: 40919, 81: 41305, 82: 41822, 83: 42122, 84: 42626, 85: 42956, 86: 43519, 87: 43751, 88: 44246, 89: 44839, 90: 45298, 91: 45423, 92: 45696, 93: 45968, 94: 463

In [62]:
tubeGraph = nx.Graph()

for connection_id, connection in connections.iterrows():
    station1_name = stations.ix[connection['station1']]['name']
    station2_name = stations.ix[connection['station2']]['name']
    tubeGraph.add_edge(station1_name, station2_name, time = connection['time'])
    
#add the connection between Bank and Monument manually
tubeGraph.add_edge('Bank', 'Monument', time = 1)
# nx.draw(tubeGraph)

/usr/local/Cellar/ipython/6.5.0/libexec/vendor/lib/python3.7/site-packages/ipykernel_launcher.py:4: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  after removing the cwd from sys.path.
/usr/local/Cellar/ipython/6.5.0/libexec/vendor/lib/python3.7/site-packages/ipykernel_launcher.py:5: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  """


In [63]:
# Example Shortest Path
nx.shortest_path(tubeGraph, 'Holborn', 'Rotherhithe', weight='time')

['Holborn',
 'Chancery Lane',
 "St. Paul's",
 'Bank',
 'Shadwell',
 'Wapping',
 'Rotherhithe']

In [64]:
# Construct graph. Code from: github.com/markdunne
normed = stations[['longitude', 'latitude']]
normed = normed - normed.min()
normed = normed / normed.max()
locations = dict(zip(stations['name'], normed[['longitude', 'latitude']].values))

p = figure(
    x_range = (.4,.7),
    y_range = (.2,.5),
    height= 700,
    width= 900,
)
for edge in tubeGraph.edges():
    p.line( 
        x= [locations[pt][0] for pt in edge],
        y= [locations[pt][1] for pt in edge],
    )

for node in tubeGraph.nodes():
    x = [locations[node][0]]
    y = [locations[node][1]]
    p.circle(
        x, y, 
        line_alpha=0)
    p.text(
        x, y, 
        text = {'value':node}, 
        text_font_size = str(10) +"pt",
        text_align='center',
        text_font_style='bold')
    
show(p)

In [65]:
# You can do graphs things on the graph.
nx.algorithms.connectivity.cuts.minimum_node_cut(tubeGraph)

{'Paddington'}

In [66]:
bikeDockingStations
#bikeDockingStations.get_value(4,"station__name")
#bikeTripData

station__name  \
station__id                                                  
1                               River Street , Clerkenwell   
2                           Phillimore Gardens, Kensington   
3                     Christopher Street, Liverpool Street   
4                          St. Chad's Street, King's Cross   
5                            Sedding Street, Sloane Square   
6                           Broadcasting House, Marylebone   
7                        Charlbert Street, St. John's Wood   
8                                   Maida Vale, Maida Vale   
9                                 New Globe Walk, Bankside   
10                                   Park Street, Bankside   
11                            Brunswick Square, Bloomsbury   
12                                Malet Street, Bloomsbury   
13                                 Scala Street, Fitzrovia   
14                          Belgrove Street , King's Cross   
15                        Great Russell Street, Bloomsbury   
16                         Cartwright Gardens , Bloomsbury   
17                                    Hatton Wall, Holborn   
18                               Drury Lane, Covent Garden   
19                              Taviton Street, Bloomsbury   
21                        Hampstead Road (Cartmel), Euston   
22                            Northington Street , Holborn   
23                                Red Lion Square, Holborn   
24                              British Museum, Bloomsbury   
25                                 Doric Way , Somers Town   
26                             Ampton Street , Clerkenwell   
27                                 Bouverie Street, Temple   
28                              Bolsover Street, Fitzrovia   
29                                Hereford Road, Bayswater   
30                                 Windsor Terrace, Hoxton   
31                                  Fanshaw Street, Hoxton   
...                                                    ...   
802                               Albert Square, Stockwell   
803                             Southwark Street, Bankside   
804                               Good's Way, King's Cross   
805                       Bevington Road, North Kensington   
806                         Handyside Street, King's Cross   
807                  Bevington Road West, North Kensington   
808                        Stockwell Roundabout, Stockwell   
809                          Lincoln's Inn Fields, Holborn   
810                                  Tate Modern, Bankside   
811                         Westferry Circus, Canary Wharf   
812          Here East North, Queen Elizabeth Olympic Park   
813                      New Spring Gardens Walk, Vauxhall   
814                Clapham Road, Lingham Street, Stockwell   
815                          Lambeth Palace Road, Waterloo   
816          Here East South, Queen Elizabeth Olympic Park   
817                            Riverlight South, Nine Elms   
818                           One Tower Bridge, Bermondsey   
819                           Belvedere Road 2, South Bank   
820                                Victory Place, Walworth   
821                Battersea Power Station, Battersea Park   
826                             Allington Street, Victoria   
828                               Normandy Road, Stockwell   
829                                  Wynne Road, Stockwell   
830                                 Sidney Road, Stockwell   
831                            St John's Crescent, Brixton   
832                                Ferndale Road, Brixton.   
833                                  Saltoun Road, Brixton   
835                             Farringdon Street, Holborn   
836                                  York Way, Kings Cross   
838                          Fore Street Avenue, Guildhall   

             station__terminalName  station__lat  station__long  \
station__id                                                       
1   

In [67]:
# Calculate the farthest bike station from the center.
maxDistance = 0
maxStationName = ''
maxStationId = -1

# Center of London
center = (51.510776, -0.115638)

for id, station in bikeDockingStations.iterrows():
    
    Lat = station["station__lat"]
    Long = station["station__long"]
    Distance = math.sqrt((Lat*(11/7))**2 + (Long)**2)
    
    if Distance > maxDistance:
        maxStationName = station["station__name"]
        maxStationId = id
        maxDistance = Distance
        
print("Furthest Docking Station:",maxStationName, " - ",maxStationId)
print(bikeDockingStations.at[maxStationId,"station__lat"], bikeDockingStations.at[maxStationId,"station__long"])



Furthest Docking Station: Lee Valley VeloPark, Queen Elizabeth Olympic Park  -  786
51.549369 -0.015717613999999998


In [186]:
###################### START OF THE COMPUTATION #####################

In [187]:
# ------------- Get Random value and Mean -----------------

def randomCoordinate():
    # Calcuates mean coordinates based on Tube Stations
    latcoors = stationsRein['latitude']
    longcoors = stationsRein['longitude']
    latmean = latcoors.mean()
    longmean = longcoors.mean()

    meancoors = (latmean, longmean)
    meancoors = (51.510776, -0.115638) # Center of London
    # print("Mean Coordinates: ", meancoors)

    latitudeBoundSize = 0.03  # Mess with these for bigger radius
    longitudeBoundSize = 0.1  # Mess with these for bigger radius

    randLat1 = meancoors[0] + (random.uniform(0,1)*latitudeBoundSize - (latitudeBoundSize/2))
    randLong1 = meancoors[1] + (random.uniform(0,1)*longitudeBoundSize - (longitudeBoundSize/2))
    randLat2 = meancoors[0] + (random.uniform(0,1)*latitudeBoundSize - (latitudeBoundSize/2))
    randLong2 = meancoors[1] + (random.uniform(0,1)*longitudeBoundSize - (longitudeBoundSize/2))

    print("Random origin location:        ", randLat1,"," ,randLong1)
    print("Random destination location:   ", randLat2,",", randLong2)
    
    return randLat1, randLong1, randLat2, randLong2

In [188]:
def getRandomBikeTrip():
    
    randIdx = -1
    dataPotentiallyDangerous = True
    while (dataPotentiallyDangerous):
        # Get random index between 0 and size of bikeTripData
        randIdx = random.randint(0,len(bikeTripData))
        
        dataPotentiallyDangerous = False
        
        # Try it
        try:
            randomStationId1 = int(bikeTripData.at[int(randIdx),"StartStation Id"])
            randomStationId2 = int(bikeTripData.at[int(randIdx),"EndStation Id"])
            bikeDockingStations.at[int(randomStationId1), "station__lat"]
            bikeDockingStations.at[int(randomStationId2), "station__lat"]
    
        except Exception:
            dataPotentiallyDangerous = True
            
        
    
    
    # Choose a random bike trip
    randomStationId1 = int(bikeTripData.at[int(randIdx),"StartStation Id"])
    randomStationId2 = int(bikeTripData.at[int(randIdx),"EndStation Id"])
    randomTripDuration = int(bikeTripData.at[int(randIdx),"Duration"])

    
    # Get the latitude and longitude of a trip
    randLat1  =  bikeDockingStations.at[int(randomStationId1), "station__lat"]
    randLong1 =  bikeDockingStations.at[int(randomStationId1), "station__long"]
    randLat2  =  bikeDockingStations.at[int(randomStationId2), "station__lat"]
    randLong2 =  bikeDockingStations.at[int(randomStationId2), "station__long"]
        
    
    print(randomStationId1)
    print(randomStationId2)

    print(randomTripDuration/60)
    
    
    # Calculate the distance in miles.
    coorDistance = math.sqrt((randLat1 - randLat2)**2 + ((randLong1 - randLong2)*(70/111))**2)*(68.9722)
    
    print(coorDistance)
    
    return randLat1, randLong1, randLat2, randLong2, randomStationId1, randomStationId2, coorDistance
    
    
getRandomBikeTrip()
    

393
54
4.0
0.5003424542518455


(51.51733427,
 -0.10360424800000001,
 51.52174785,
 -0.094475072,
 393,
 54,
 0.5003424542518455)

In [189]:
# --------------- Calculates the closest TUBE stations to the random coordinates --------------

def closestTubeStation(randLat1, randLong1, randLat2, randLong2):
    #calculate distances to all stations in array from co-ordinates
    tubeDistances1 = []
    tubeDistances2 = []
    for i in range(1, len(stationsRein['longitude'])):
        distance1 = math.sqrt(((randLat1 - stationsRein['latitude'].iloc[i-1])*(11/7))**2 + (randLong1 - stationsRein['longitude'].iloc[i-1])**2)
        distance2 = math.sqrt(((randLat2 - stationsRein['latitude'].iloc[i-1])*(11/7))**2 + (randLong2 - stationsRein['longitude'].iloc[i-1])**2)

        tubeDistances1.append(distance1)
        tubeDistances2.append(distance2)

    #pick shortest for each co-ordinate
    station1 = tubeDistances1.index(min(tubeDistances1))
    station2 = tubeDistances2.index(min(tubeDistances2))
    
    oName = stationsRein['name'][station1+1]
    oLat  = stationsRein['latitude'][station1+1]
    oLong = stationsRein['longitude'][station1+1]
    
    dName = stationsRein['name'][station2+1]
    dLat  = stationsRein['latitude'][station2+1]
    dLong = stationsRein['longitude'][station2+1]

    print("Nearest train station to Random Origin:",oName,oLat,oLong)
    print("Nearest train station to Random Destination:",dName,dLat,dLong)
    
    return oName, dName
    #return oName,oLat,oLong,dName,dLat,dLong

In [190]:
# ---------------- Calculate the closest BIKE station to the random coordinates ---------------

def closestBikeStation(randLat1, randLong1, randLat2, randLong2):

    shortestOriginID = -1
    shortestDestID = -1
    
    shortestBikeOriginValue = 9999
    shortestBikeDestinationValue = 9999

    for st_id, dockingStation in bikeDockingStations.iterrows():
        dockingID = st_id
        dockingLat  = dockingStation["station__lat"]
        dockingLong = dockingStation["station__long"]
        distanceFromRandomToOrigin      = math.sqrt(((randLat1 - dockingLat)*11/7)**2 + (randLong1 - dockingLong)**2)
        distanceFromRandomToDestination = math.sqrt(((randLat2 - dockingLat)*11/7)**2 + (randLong2 - dockingLong)**2)

        if distanceFromRandomToOrigin < shortestBikeOriginValue:
            shortestOriginID = dockingID
            shortestBikeOriginValue = distanceFromRandomToOrigin

        if distanceFromRandomToDestination < shortestBikeDestinationValue:
            shortestDestID = dockingID
            shortestBikeDestinationValue = distanceFromRandomToDestination

    print("Nearest bike station to Random Origin:", shortestOriginID)
    print("Nearest bike station to Random Destination:", shortestDestID)
    
    return shortestOriginID, shortestDestID

In [191]:
# ------------- Calculate BIKE travel time -----------------------
# Calculates the mean of the closest bike ports, as well as ones that are really close.

def calcBikeTravelTimeMins(oBikeStationID, dBikeStationID):
    exactMatches = 0
    #relativeMatches = 0
    totalDurationAllTrips = 0
    
    # Get the range of samples to look at 
    # As an optimization, only looked at the subset of data with the curent station station.
    try:
        lowerBound = startOfBikeDataStartStationSection[oBikeStationID]
        upperBound = startOfBikeDataStartStationSection[oBikeStationID +1] - 1
    except Exception:
        return -1
    
    if lowerBound == 0:
        lowerBound = 1
    
    print(oBikeStationID,lowerBound,upperBound)
    
    for i in range(lowerBound, upperBound):

        # Extract the trip data.
        tStartName =  bikeTripData.at[int(i),"StartStation Name"]
        tStartID =    bikeTripData.at[int(i),"StartStation Id"]

        tEndName   =  bikeTripData.at[int(i),"EndStation Name"]
        tEndID =  bikeTripData.at[int(i),"EndStation Id"]
        
        tDuration = bikeTripData.at[int(i),"Duration"]
        
        # If this trip exactly matches the given origin and dest.
        if oBikeStationID == tStartID and dBikeStationID == tEndID:
            exactMatches += 1
            totalDurationAllTrips += tDuration
            
            
    print("For bikes there were:",exactMatches, "exact matches.")
#   print("For bikes there were:",relativeMatches, "relative matches.")
    
    if exactMatches == 0:
        return -1 # ERROR! No matches...
    
    bikeMins = (totalDurationAllTrips / (exactMatches))/60
    print("The average time of this BIKE trip is:", bikeMins, "minutes.")
    
    
    return bikeMins

In [192]:
# --------------- Calculate TRAIN travel time --------------
# Calculates with dijkstra's shortest path algorithm (weighted by TIME)
def calcTrainTravelTimeMins(oName, dName):
    
    #nx.algorithms.shortest_paths.dijkstra_path(tubeGraph, oName, dName)

    quickestTrainTime = nx.algorithms.shortest_paths.dijkstra_path_length(tubeGraph,oName,dName, weight = "time")

    print("The quickest time for this TRAIN trip is ",quickestTrainTime, "minutes.")
    
    return quickestTrainTime

In [193]:
#### ------ Calculate how far the trip actually is------- ####

#distance1 = math.sqrt(((randLat1 - stationsRein['latitude'].iloc[i-1])*(11/7))**2 + (randLong1 - stationsRein['longitude'].iloc[i-1])**2)
#distance2 = math.sqrt(((randLat2 - stationsRein['latitude'].iloc[i-1])*(11/7))**2 + (randLong2 - stationsRein['longitude'].iloc[i-1])**2)

In [195]:
########## RUN ME ############
numIterations = 10000


##############################

output = {}
for i in range(0, numIterations):
    print("[!] Iteration", i)
    # Compute random coordinates in our range
    #(randLat1, randLong1, randLat2, randLong2) = randomCoordinate()
    (randLat1, randLong1, randLat2, randLong2, oBike, dBike, coorDistance) = getRandomBikeTrip()

    # Calculate the nearest origin and destination stations, given the random coordinates.
    (oTrain,dTrain) = closestTubeStation(randLat1, randLong1, randLat2, randLong2)
##    (oBike, dBike) = closestBikeStation(randLat1, randLong1, randLat2, randLong2)

    # Calculate the minimum/average travel time (with our data) given an origin and a destination.
    trainMins = calcTrainTravelTimeMins(oTrain,dTrain)
    bikeMins = calcBikeTravelTimeMins(oBike, dBike)

    if bikeMins == -1 or trainMins == -1:
        print("error")
        continue
        
    output[i] = {"oRandomLat": randLat1,
                 "oRandomLong": randLong1,
                 "dRandomLat": randLat2,
                 "dRandomLong": randLong2,
                 "coorDistance": coorDistance,
                 "oTrain": oTrain, 
                 "dTrain": dTrain,
                 "oBike": oBike,
                 "dBike": dBike,
                 "bikeMins": bikeMins,
                 "trainMins": trainMins}
    



[!] Iteration 0
321
314
8.0
0.21985491425301132
Nearest train station to Random Origin: London Bridge 51.5052 -0.0864
Nearest train station to Random Destination: London Bridge 51.5052 -0.0864
The quickest time for this TRAIN trip is  0 minutes.
321 153689 154405
For bikes there were: 8 exact matches.
The average time of this BIKE trip is: 5.625 minutes.
[!] Iteration 1
253
588
6.0
0.4110171123633985
Nearest train station to Random Origin: Old Street 51.5263 -0.0873
Nearest train station to Random Destination: Old Street 51.5263 -0.0873
The quickest time for this TRAIN trip is  0 minutes.
253 126412 126926
For bikes there were: 7 exact matches.
The average time of this BIKE trip is: 5.2857142857142865 minutes.
[!] Iteration 2
66
374
9.0
0.9866018883328855
Nearest train station to Random Origin: Chancery Lane 51.5185 -0.1111
Nearest train station to Random Destination: Waterloo 51.5036 -0.1143
The quickest time for this TRAIN trip is  8 minutes.
66 33223 34180
For bikes there were: 14 e

Nearest train station to Random Origin: Mornington Crescent 51.5342 -0.1387
Nearest train station to Random Destination: Tottenham Court Road 51.5165 -0.131
The quickest time for this TRAIN trip is  6 minutes.
362 171499 171830
For bikes there were: 2 exact matches.
The average time of this BIKE trip is: 14.0 minutes.
[!] Iteration 24
404
404
3.0
0.0
Nearest train station to Random Origin: High Street Kensington 51.5009 -0.1925
Nearest train station to Random Destination: High Street Kensington 51.5009 -0.1925
The quickest time for this TRAIN trip is  0 minutes.
404 186798 187785
For bikes there were: 150 exact matches.
The average time of this BIKE trip is: 50.86 minutes.
[!] Iteration 25
219
432
8.0
0.8570822663949462
Nearest train station to Random Origin: West Brompton 51.4872 -0.1953
Nearest train station to Random Destination: South Kensington 51.4941 -0.1738
The quickest time for this TRAIN trip is  5 minutes.
219 110288 110787
For bikes there were: 9 exact matches.
The average 

For bikes there were: 25 exact matches.
The average time of this BIKE trip is: 27.040000000000003 minutes.
[!] Iteration 53
550
495
8.0
1.0036662882435357
Nearest train station to Random Origin: Stepney Green 51.5221 -0.047
Nearest train station to Random Destination: Bow Church 51.5273 -0.0208
The quickest time for this TRAIN trip is  10 minutes.
550 229768 229996
For bikes there were: 4 exact matches.
The average time of this BIKE trip is: 8.5 minutes.
[!] Iteration 54
591
733
21.0
3.193213886671466
Nearest train station to Random Origin: Shepherd's Bush (H) 51.5058 -0.2265
Nearest train station to Random Destination: Hyde Park Corner 51.5027 -0.1527
The quickest time for this TRAIN trip is  16 minutes.
591 242782 243096
For bikes there were: 1 exact matches.
The average time of this BIKE trip is: 21.0 minutes.
[!] Iteration 55
148
366
13.0
1.4109944114756783
Nearest train station to Random Origin: Pimlico 51.4893 -0.1334
Nearest train station to Random Destination: Bond Street 51.51

Nearest train station to Random Origin: Limehouse 51.5123 -0.0396
Nearest train station to Random Destination: Stepney Green 51.5221 -0.047
The quickest time for this TRAIN trip is  7 minutes.
480 208866 209437
For bikes there were: 9 exact matches.
The average time of this BIKE trip is: 6.111111111111112 minutes.
[!] Iteration 80
781
635
17.0
1.925074862539551
Nearest train station to Random Origin: South Kensington 51.4941 -0.1738
Nearest train station to Random Destination: Barons Court 51.4905 -0.2139
The quickest time for this TRAIN trip is  6 minutes.
781 297980 298324
For bikes there were: 3 exact matches.
The average time of this BIKE trip is: 17.0 minutes.
[!] Iteration 81
792
139
9.0
0.9348401244941358
Nearest train station to Random Origin: Southwark 51.501000000000005 -0.1052
Nearest train station to Random Destination: Lambeth North 51.4991 -0.1115
The quickest time for this TRAIN trip is  2 minutes.
792 301987 302452
For bikes there were: 6 exact matches.
The average time

Nearest train station to Random Origin: Marylebone 51.5225 -0.1631
Nearest train station to Random Destination: Baker Street 51.5226 -0.1571
The quickest time for this TRAIN trip is  1 minutes.
605 246782 247148
For bikes there were: 7 exact matches.
The average time of this BIKE trip is: 2.8571428571428568 minutes.
[!] Iteration 109
85
156
8.0
0.755976000553606
Nearest train station to Random Origin: London Bridge 51.5052 -0.0864
Nearest train station to Random Destination: Elephant & Castle 51.4943 -0.1001
The quickest time for this TRAIN trip is  3 minutes.
85 42956 43518
For bikes there were: 2 exact matches.
The average time of this BIKE trip is: 7.5 minutes.
[!] Iteration 110
248
307
18.0
0.8002641859123456
Nearest train station to Random Origin: Lancaster Gate 51.5119 -0.1756
Nearest train station to Random Destination: Queensway 51.5107 -0.1877
The quickest time for this TRAIN trip is  1 minutes.
248 122695 124216
For bikes there were: 73 exact matches.
The average time of this

...

Nearest train station to Random Origin: London Bridge 51.5052 -0.0864
Nearest train station to Random Destination: London Bridge 51.5052 -0.0864
The quickest time for this TRAIN trip is  0 minutes.
818 310039 310539
For bikes there were: 13 exact matches.
The average time of this BIKE trip is: 3.6923076923076925 minutes.
[!] Iteration 9870
411
24
16.0
2.0799301819942917
Nearest train station to Random Origin: Elephant & Castle 51.4943 -0.1001
Nearest train station to Random Destination: Holborn 51.5174 -0.12
The quickest time for this TRAIN trip is  10 minutes.
411 189502 189978
For bikes there were: 3 exact matches.
The average time of this BIKE trip is: 15.666666666666666 minutes.
[!] Iteration 9871
177
383
13.0
1.2428888059877894
Nearest train station to Random Origin: Victoria 51.4965 -0.1447
Nearest train station to Random Destination: Leicester Square 51.5113 -0.1281
The quickest time for this TRAIN trip is  5 minutes.
177 87410 88333
For bikes there were: 8 exact matches.
The av

Nearest train station to Random Origin: Mansion House 51.5122 -0.094
Nearest train station to Random Destination: Chancery Lane 51.5185 -0.1111
The quickest time for this TRAIN trip is  8 minutes.
427 192626 193842
For bikes there were: 5 exact matches.
The average time of this BIKE trip is: 12.4 minutes.
[!] Iteration 9895
301
826
14.0
1.2546240440197474
Nearest train station to Random Origin: Bond Street 51.5142 -0.1494
Nearest train station to Random Destination: Victoria 51.4965 -0.1447
The quickest time for this TRAIN trip is  4 minutes.
301 145549 146006
For bikes there were: 5 exact matches.
The average time of this BIKE trip is: 13.0 minutes.
[!] Iteration 9896
301
428
25.0
1.53995370704625
Nearest train station to Random Origin: Bond Street 51.5142 -0.1494
Nearest train station to Random Destination: South Kensington 51.4941 -0.1738
The quickest time for this TRAIN trip is  8 minutes.
301 145549 146006
For bikes there were: 3 exact matches.
The average time of this BIKE trip i

For bikes there were: 13 exact matches.
The average time of this BIKE trip is: 11.615384615384615 minutes.
[!] Iteration 9919
95
132
21.0
1.0012566260870768
Nearest train station to Random Origin: Barbican 51.5204 -0.0979
Nearest train station to Random Destination: Shoreditch 51.5227 -0.0708
The quickest time for this TRAIN trip is  11 minutes.
95 46834 47743
For bikes there were: 20 exact matches.
The average time of this BIKE trip is: 13.05 minutes.
[!] Iteration 9920
479
152
38.0
3.0670380808899163
Nearest train station to Random Origin: Bethnal Green 51.527 -0.0549
Nearest train station to Random Destination: Elephant & Castle 51.4943 -0.1001
The quickest time for this TRAIN trip is  10 minutes.
479 208354 208865
For bikes there were: 1 exact matches.
The average time of this BIKE trip is: 38.0 minutes.
[!] Iteration 9921
732
331
8.0
1.010324742161007
Nearest train station to Random Origin: London Bridge 51.5052 -0.0864
Nearest train station to Random Destination: Moorgate 51.5186

[!] Iteration 9946
237
458
6.0
0.5779208115396561
Nearest train station to Random Origin: Tower Gateway 51.5106 -0.0743
Nearest train station to Random Destination: Wapping 51.5043 -0.0558
The quickest time for this TRAIN trip is  3 minutes.
237 118856 119267
For bikes there were: 5 exact matches.
The average time of this BIKE trip is: 5.8 minutes.
[!] Iteration 9947
618
737
2.0
0.2561167640407493
Nearest train station to Random Origin: Fulham Broadway 51.4804 -0.195
Nearest train station to Random Destination: Fulham Broadway 51.4804 -0.195
The quickest time for this TRAIN trip is  0 minutes.
618 250195 250490
For bikes there were: 25 exact matches.
The average time of this BIKE trip is: 60.32 minutes.
[!] Iteration 9948
350
187
6.0
0.6399967783541575
Nearest train station to Random Origin: Gloucester Road 51.4945 -0.1829
Nearest train station to Random Destination: South Kensington 51.4941 -0.1738
The quickest time for this TRAIN trip is  1 minutes.
350 165129 165948
For bikes there 

For bikes there were: 4 exact matches.
The average time of this BIKE trip is: 11.0 minutes.
[!] Iteration 9979
104
184
29.0
3.027726380743242
Nearest train station to Random Origin: Tower Hill 51.5098 -0.0766
Nearest train station to Random Destination: Regent's Park 51.5234 -0.1466
The quickest time for this TRAIN trip is  14 minutes.
104 52009 53266
For bikes there were: 4 exact matches.
The average time of this BIKE trip is: 26.75 minutes.
[!] Iteration 9980
233
130
32.0
2.405709766251904
Nearest train station to Random Origin: Picadilly Circus 51.5098 -0.1342
Nearest train station to Random Destination: Tower Hill 51.5098 -0.0766
The quickest time for this TRAIN trip is  12 minutes.
233 117099 117660
For bikes there were: 3 exact matches.
The average time of this BIKE trip is: 27.0 minutes.
[!] Iteration 9981
803
229
27.0
1.0832035376521987
Nearest train station to Random Origin: Borough 51.5011 -0.0943
Nearest train station to Random Destination: Embankment 51.5074 -0.1223
The qui

In [196]:
dataFrame = pd.DataFrame.from_dict(output, orient="index")
dataFrame

oRandomLat  oRandomLong  dRandomLat  dRandomLong  coorDistance  \
0      51.497856    -0.081608   51.500889    -0.083159      0.219855   
1      51.534043    -0.086380   51.529590    -0.080100      0.411017   
2      51.517950    -0.108657   51.504028    -0.113864      0.986602   
3      51.517607    -0.121328   51.539084    -0.070329      2.667379   
4      51.517950    -0.108657   51.490164    -0.190394      4.038864   
5      51.530992    -0.093904   51.507770    -0.130700      2.264227   
6      51.503118    -0.153521   51.516780    -0.175489      1.342000   
7      51.516155    -0.082422   51.503920    -0.113426      1.590812   
8      51.529944    -0.123617   51.513528    -0.130111      1.166960   
9      51.511962    -0.097442   51.503920    -0.113426      0.889416   
10     51.504719    -0.063531   51.518154    -0.062697      0.927351   
11     51.506304    -0.087263   51.485821    -0.149004      3.034435   
12     51.512529    -0.115163   51.504028    -0.113864      0.589051   
13     51.507385    -0.096441   51.508447    -0.055167      1.796735   
14     51.477839    -0.116493   51.495656    -0.114605      1.231619   
15     51.472817    -0.199783   51.477276    -0.189210      0.553240   
16     51.510048    -0.138846   51.514760    -0.148105      0.517490   
17     51.493373    -0.099681   51.523418    -0.124122      2.329092   
18     51.475051    -0.150908   51.475051    -0.150908      0.000000   
19     51.519069    -0.088285   51.518219    -0.100791      0.547100   
20     51.517075    -0.086686   51.520842    -0.097340      0.531279   
21     51.500089    -0.116629   51.477871    -0.126874      1.595934   
22     51.531066    -0.119340   51.522853    -0.099994      1.014376   
23     51.536264    -0.133952   51.517727    -0.127854      1.305756   
24     51.502042    -0.184400   51.502042    -0.184400      0.000000   
25     51.490164    -0.190394   51.496957    -0.173894      0.857082   
26     51.485917    -0.124470   51.512484    -0.099141      2.138091   
27     51.509943    -0.117619   51.507425    -0.134621      0.759649   
28     51.532513    -0.033085   51.520893    -0.051394      1.129839   
29     51.515419    -0.098851   51.510485    -0.082990      0.769260   
...          ...          ...         ...          ...           ...   
9970   51.523196    -0.083067   51.515810    -0.105270      1.091878   
9971   51.519362    -0.074431   51.503494    -0.079621      1.117503   
9972   51.529537    -0.083353   51.518908    -0.079249      0.754535   
9973   51.538718    -0.011889   51.538718    -0.011889      0.000000   
9974   51.505014    -0.173060   51.505014    -0.173060      0.000000   
9975   51.493700    -0.121394   51.501445    -0.110699      0.708328   
9976   51.512276    -0.157437   51.488226    -0.135636      1.910715   
9977   51.518908    -0.079249   51.516155    -0.082422      0.234770   
9978   51.503792    -0.112824   51.499076    -0.085666      1.225221   
9979   51.511595    -0.077121   51.520715    -0.145212      3.027726   
9980   51.507770    -0.130700   51.509506    -0.075459      2.405710   
9981   51.505410    -0.098341   51.506543    -0.123180      1.083204   
9982   51.510485    -0.082990   51.517428    -0.107987      1.188072   
9983   51.478939    -0.208485   51.494186    -0.182671      1.538355   
9984   51.518811    -0.011662   51.535179    -0.033380      1.472024   
9985   51.490164    -0.190394   51.485122    -0.174972      0.755560   
9986   51.494412    -0.173881   51.474392    -0.163348      1.454837   
9987   51.528869    -0.047548   51.518908    -0.079249      1.540547   
9988   51.515975    -0.053177   51.528169    -0.018703      1.719245   
9989   51.527068    -0.131861   51.527068    -0.131861      0.000000   
9990   51.529944    -0.123617   51.518219    -0.100791      1.280514   
9991   51.518118    -0.144229   51.513528    -0.130111      0.690891   
9992   51.527026    -0.088543   51.486343    -0.122492      3.170785   
9993   51.506946    -0.058681   51.528187    -

In [197]:
dataFrame.to_csv("./londonComputedData/computedData.csv")


In [129]:
#calcBikeTravelTimeMins(751,95)


In [126]:
#bikeDockingStations.at[int(4),"station__lat"]


In [128]:
#bikeTripData